# CARACTERIZATION OF COORDINATES AND REFRESH RATES OF THE GPS

In [1]:
import pandas as pd
import geopandas as gpd
import statsmodels.api as sm

import datetime
from datetime import timedelta

import statistics
import math

import plotly.graph_objects as go
import plotly.figure_factory as ff
import plotly.express as px

from shapely.geometry import shape
from shapely.geometry import Point, LineString

pd.set_option("display.precision", 9)

In [2]:
#Route and lines shape
route_lines = gpd.read_file('M6Data/route_lines.json',geometry='geometry')
line1 = route_lines.loc[(route_lines['line_id']=='1')&(route_lines['direction']=='1')]
line2 = route_lines.loc[(route_lines['line_id']=='1')&(route_lines['direction']=='2')]
route_lines.head()

itinerary_id line_id direction  orig_dist    dist  \
0  6_N_501____1__IT_1     501         1     84.910  20.429   
1  6_N_501____2__IT_1     501         2     42.932  13.472   
2  6_N_502____1__IT_1     502         1     60.927  19.403   
3  6_N_502____2__IT_1     502         2     96.684  21.195   
4  6_N_503____1__IT_1     503         1     31.595  14.011   

                                            geometry  
0  LINESTRING (-3.69234 40.41997, -3.69193 40.420...  
1  LINESTRING (-3.64667 40.48592, -3.64668 40.485...  
2  LINESTRING (-3.69269 40.41872, -3.69269 40.418...  
3  LINESTRING (-3.61127 40.49814, -3.61091 40.498...  
4  LINESTRING (-3.69269 40.41872, -3.69269 40.418...

In [3]:
#Stops
stops = gpd.read_file('M6Data/stops.json',geometry='geometry')
stops.head()

stop_code                stop_name                    stop_desc zone_id  \
0        161         Puerta de Alcalá  Plaza de la Independencia 3       A   
1        162                   Retiro            Avda de Méjico SN       A   
2        164  Círculo de Bellas Artes           Calle   Gran Vía 3       A   
3        168            Santo Domingo           Calle  Gran Vía 56       A   
4        169            Santo Domingo           Calle  Gran Vía 47       A   

   location_type parent_station  wheelchair_boarding  \
0              0           None                    2   
1              0           None                    2   
2              0           None                    2   
3              0           None                    2   
4              0           None                    2   

                    geometry  
0  POINT (-3.68919 40.42069)  
1  POINT (-3.68826 40.41970)  
2  POINT (-3.69715 40.41896)  
3  POINT (-3.70761 40.42159)  
4  POINT (-3.70746 40.42114)

In [4]:
#Experiment data
experiment = pd.read_csv('experiment.csv')
experiment = experiment[['bus','line','stop','datetime','isHead','destination','request_time','estimateArrive','DistanceBus','given_coords','lat','lon']]
experiment = experiment.loc[(experiment.estimateArrive < 999999) & (experiment.DistanceBus >= 0)]
experiment = experiment.loc[((experiment.DistanceBus == 0) & (experiment.estimateArrive == 0)) | ((experiment.DistanceBus > 0) & (experiment.estimateArrive > 0))]
experiment['datetime'] = pd.to_datetime(experiment['datetime'], format='%Y-%m-%d %H:%M:%S.%f')
experiment = experiment.sort_values(by=['datetime']).reset_index()
experiment.head()

index   bus  line  stop                   datetime  isHead  destination  \
0      9   120     1  5137 2020-03-04 21:16:46.148241   False   CRISTO REY   
1      8  8224     1  5137 2020-03-04 21:16:46.148241   False   CRISTO REY   
2    113  8224     1   736 2020-03-04 21:16:46.160914   False   CRISTO REY   
3    112   117     1   736 2020-03-04 21:16:46.160914   False   CRISTO REY   
4     68   118     1   717 2020-03-04 21:16:46.184715   False  PROSPERIDAD   

   request_time  estimateArrive  DistanceBus  given_coords           lat  \
0            98            1462         4355             1  40.439677241   
1            98              11            6             1  40.429767628   
2           126             739         1870             1  40.429767628   
3           126             135          553             1  40.420987214   
4           128            1038         3250             1  40.423773102   

           lon  
0 -3.673392522  
1 -3.672571358  
2 -3.672571358  
3 -3.688482726  
4 -3.710763993

In [5]:
experiment.describe()

index              bus     line             stop  \
count  38557.000000000  38557.000000000  38557.0  38557.000000000   
mean   19361.153720466   3551.007132298      1.0   1217.344399201   
std    11206.216782207   4078.758474945      0.0   1496.437324963   
min        0.000000000    116.000000000      1.0      9.000000000   
25%     9660.000000000    117.000000000      1.0    423.000000000   
50%    19315.000000000    120.000000000      1.0    724.000000000   
75%    29085.000000000   8238.000000000      1.0    738.000000000   
max    38810.000000000   8633.000000000      1.0   5138.000000000   

          request_time   estimateArrive      DistanceBus     given_coords  \
count  38557.000000000  38557.000000000  38557.000000000  38557.000000000   
mean     137.899421636    912.516067121   2460.783126281      0.750992038   
std       66.284979952    589.838291498   1622.477805341      0.432444039   
min       56.000000000      0.000000000      0.000000000      0.000000000   
25%      103.000000000    410.000000000   1092.000000000      1.000000000   
50%      125.000000000    880.000000000   2360.000000000      1.000000000   
75%      156.000000000   1364.000000000   3617.000000000      1.000000000   
max     1201.000000000   2698.000000000   7419.000000000      1.000000000   

                   lat              lon  
count  38557.000000000  38557.000000000  
mean      40.427538177     -3.691620385  
std        0.008252357      0.013706503  
min       40.418555858     -3.719073428  
25%       40.419973216     -3.701846724  
50%       40.425890302     -3.690537244  
75%       40.430619822     -3.678028898  
max       40.444293137     -3.669923246

## GPS REFRESH RATE ANALYSIS

In [6]:
#Buses with given coords
buses_calc = experiment.loc[experiment.given_coords == 0].bus.unique().tolist()
buses_given = experiment.loc[~experiment.bus.isin(buses_calc)].bus.unique().tolist()

In [7]:
#Standard deviation of the location values
def std_buses (df) :
    std_buses_dict = {}
    for bus in df.bus.unique() : 
        bus_df = df.loc[df.bus == bus]
        if  True :#bus_df.given_coords.min() == 1 :
            std_buses_dict[bus] = {}
            std_buses_dict[bus]['lat'] = bus_df.lat.std()
            std_buses_dict[bus]['lon'] = bus_df.lon.std()
    
    return std_buses_dict

std_buses(experiment)

{120: {'lat': 0.001317540399853089, 'lon': 0.0012325701750561698},
 8224: {'lat': 0.0031688155964841205, 'lon': 0.00510784879045711},
 117: {'lat': 0.000729395849912889, 'lon': 0.0041017155934388394},
 118: {'lat': 0.0015846846207229308, 'lon': 0.005477931800098498},
 8238: {'lat': 0.004197048913434349, 'lon': 0.005531970250069568},
 8633: {'lat': 0.0047076446754644105, 'lon': 0.009211916566569485},
 116: {'lat': 0.004170571160310396, 'lon': 0.011944771117962423},
 4705: {'lat': 7.20343788209521e-15, 'lon': 9.004297352619012e-16}}

In [8]:
#Number of repeated values for lat or lon values for a bus
experiment.loc[experiment.bus == 116].lat.value_counts()

40.419663029    20
40.432215908    17
40.420118088    17
40.421115849    16
40.419588795    15
                ..
40.418995541     1
40.427399116     1
40.426676829     1
40.427428559     1
40.419075672     1
Name: lat, Length: 4168, dtype: int64

In [9]:
#Mean time transcurred before new value of location
def gps_update_time(df):
    update_time_buses_dict = {}
    for bus in df.bus.unique() : 
        bus_df = df.loc[df.bus == bus]
        if True : #bus_df.given_coords.min() == 1 :
            last_lat = bus_df.iloc[0].lat
            last_time = bus_df.iloc[0].datetime
            update_times = []
            for index,row in bus_df.iterrows() :
                if row.DistanceBus == 0 :
                    last_lat = row.lat
                    last_time = row.datetime
                elif last_lat != row.lat :
                    update_seconds = (row.datetime - last_time).total_seconds()
                    update_times.append(update_seconds)
                    last_lat = row.lat
                    last_time = row.datetime
            if len(update_times) != 0 :
                update_time_buses_dict[bus] = {}
                update_time_buses_dict[bus]['mean'] = statistics.mean(update_times)
                update_time_buses_dict[bus]['all'] = update_times
    
    return update_time_buses_dict

update_time_buses_dict = gps_update_time(experiment)

In [10]:
fig1 = go.Figure()
# Create and style traces
for bus in update_time_buses_dict.keys() :
    fig1.add_trace(go.Box(
        y=update_time_buses_dict[bus]['all'],
        name='Bus : {}'.format(bus),
        boxmean='sd' # represent mean and standard deviation
    ))
    
# Edit the layout
fig1.update_layout(title='Update times of gps (distance if the bus coords have been calculated)',
                   xaxis_title='Update number',
                   yaxis_title='Update time (seconds)')

fig1.show()

In [11]:
fig2 = go.Figure()
# Create and style traces
means = []
refresh_times = []
for bus in buses_given :
    if bus in update_time_buses_dict.keys() :
        refresh_times = refresh_times + update_time_buses_dict[bus]['all']
    
fig2.add_trace(go.Box(
    name='',
    y=refresh_times,
    boxmean='sd' # represent mean and standard deviation
))
    
# Edit the layout
fig2.update_layout(title='Update times of gps (distance if the bus coords have been calculated)',
                   xaxis_title='Update number',
                   yaxis_title='Update time (seconds)')

fig2.show()

## Distance of the bus coordinates to the nearest point on the line

In [12]:
def haversine(coord1, coord2):
    '''
    Returns distance between two given coordinates in meters
    '''
    R = 6372800  # Earth radius in meters
    lat1, lon1 = coord1
    lat2, lon2 = coord2
    
    phi1, phi2 = math.radians(lat1), math.radians(lat2) 
    dphi       = math.radians(lat2 - lat1)
    dlambda    = math.radians(lon2 - lon1)
    
    a = math.sin(dphi/2)**2 + \
        math.cos(phi1)*math.cos(phi2)*math.sin(dlambda/2)**2
    
    return 2*R*math.atan2(math.sqrt(a), math.sqrt(1 - a))

def nearest_point_on_line (line, bus_coords) :
    """
    Returns the coordinates of the bus location
        Parameters
        ----------
        line : geometry
            The shape of the line that the bus belongs to
        bus_coords :
            The coordinates of the bus
    """
    bus_point = Point(bus_coords)
    
    #First we calculate the normalized distance of the projected point in the line to the start of the line
    normalized_distance = line.project(bus_point,normalized=True)
    
    #Then we get the the coordinates of the point that is at the normalized distance obtained 
    #before from the start of the line with the interpolate method
    interpolated_point = line.interpolate(normalized_distance,normalized=True)
    
    #And we return the coordinates of the point
    return (interpolated_point.x,interpolated_point.y)

In [13]:
destinations = ['PROSPERIDAD','CRISTO REY']
def distance_to_line(df) :
    distance_to_line_buses_dict = {}
    for bus in df.bus.unique() : 
        bus_df = df.loc[df.bus == bus]
        if bus_df.given_coords.min() == 1 :
            dest = bus_df.iloc[0].destination
            if dest == 'PROSPERIDAD' :
                line = line1
            else :
                line = line2
            #Calculate the nearest point of the line to the bus
            distances_to_line = []
            last_distance = 0
            for index,row in bus_df.iterrows() :
                nearest_point = nearest_point_on_line(line,(row.lon,row.lat))
                new_distance = haversine((row.lon,row.lat),nearest_point)
                if last_distance != new_distance :
                    distances_to_line.append(new_distance)
                    last_distance = new_distance

            if len(distances_to_line) != 0 :
                distance_to_line_buses_dict[bus] = {}
                distance_to_line_buses_dict[bus]['mean'] = statistics.mean(distances_to_line)
                distance_to_line_buses_dict[bus]['all'] = distances_to_line
        
    return distance_to_line_buses_dict

distance_to_line_buses_dict = distance_to_line(experiment)

In [29]:
fig3 = go.Figure()
for bus in distance_to_line_buses_dict.keys() :
    fig3.add_trace(go.Histogram(
        name='{}'.format(bus),
        x=distance_to_line_buses_dict[bus]['all'],
        xbins=dict( # bins used for histogram
            start=0,
            end=max(distance_to_line_buses_dict[bus]['all']),
            size=10
        )
    ))

# Overlay histograms
fig3.update_layout(
    title='Histogram of distance to the line for each bus',
    xaxis_title='Distance in meters',
    yaxis_title='Number of instances inside the interval',
    bargap=0.1, # gap between bars of adjacent location coordinates
    bargroupgap=0.05 # gap between bars of the same location coordinates
)
# Reduce opacity to see both histograms
fig3.update_traces(opacity=0.75)
fig3.show()

In [30]:
fig4 = go.Figure()
all_instances = []
for bus in distance_to_line_buses_dict.keys() :
    all_instances = all_instances + distance_to_line_buses_dict[bus]['all']

fig4.add_trace(go.Histogram(
    name='{}',
    x=all_instances,
    xbins=dict( # bins used for histogram
        start=0,
        end=max(all_instances),
        size=10
    )
))

# Overlay histograms
fig4.update_layout(
    title='Histogram of distance to the line for each bus',
    xaxis_title='Distance in meters',
    yaxis_title='Number of instances inside the interval',
    bargap=0.1, # gap between bars of adjacent location coordinates
    bargroupgap=0.05 # gap between bars of the same location coordinates
)
# Reduce opacity to see both histograms
fig4.update_traces(opacity=0.75)
fig4.show()

In [16]:
#Before applying the filter

#Sometimes when the distance is 0, the ETA is not 0
#experiment.loc[(experiment.DistanceBus == 0) & (experiment.estimateArrive != 0)].describe()
#It doesnt happen at the reverse case
#experiment.loc[(experiment.DistanceBus <= 0) & (experiment.estimateArrive == 0)].describe()

In [17]:
def distance_to_stop(df) :
    distance_to_stop_buses_dict = {}
    for bus in df.bus.unique() : 
        bus_df_all = df.loc[(df.bus == bus)].reset_index()
        bus_df = bus_df_all.loc[(bus_df_all.estimateArrive == 0) & (bus_df_all.DistanceBus == 0)]
        if True : #bus_df.given_coords.min() == 1 :
            distances_to_stop = []
            stops_points_lon,stops_points_lat = [],[]
            stopped_bus_points_lon,stopped_bus_points_lat = [],[]
            last_distance = 0
            for index,row in bus_df.iterrows() :
                stop_point = stops.loc[stops.stop_code == row.stop].iloc[0].geometry
                new_distance = haversine((row.lon,row.lat),(stop_point.x,stop_point.y))
                if last_distance != new_distance :
                    distances_to_stop.append(new_distance)
                    last_distance = new_distance
                    stops_points_lon.append(stop_point.x)
                    stops_points_lat.append(stop_point.y)
                    
                    k = index
                    #Delayed rows bus coords
                    #if (index+3500)<bus_df_all.shape[0] :
                        #k = index + 3500
                    stopped_bus_points_lon.append(bus_df_all.iloc[k].lon)
                    stopped_bus_points_lat.append(bus_df_all.iloc[k].lat)
                    
                    
            if len(distances_to_stop) != 0 :
                distance_to_stop_buses_dict[bus] = {}
                distance_to_stop_buses_dict[bus]['mean'] = statistics.mean(distances_to_stop)
                distance_to_stop_buses_dict[bus]['all'] = distances_to_stop
                distance_to_stop_buses_dict[bus]['stop_lons'] = stops_points_lon
                distance_to_stop_buses_dict[bus]['stop_lats'] = stops_points_lat
                distance_to_stop_buses_dict[bus]['bus_lons'] = stopped_bus_points_lon
                distance_to_stop_buses_dict[bus]['bus_lats'] = stopped_bus_points_lat
    
    return distance_to_stop_buses_dict

distance_to_stop_buses_dict = distance_to_stop(experiment)

In [31]:
fig5 = go.Figure()
for bus in distance_to_stop_buses_dict.keys() :
    fig5.add_trace(go.Histogram(
        name='{}'.format(bus),
        x=distance_to_stop_buses_dict[bus]['all'],
        xbins=dict( # bins used for histogram
            start=min(distance_to_stop_buses_dict[bus]['all']),
            end=max(distance_to_stop_buses_dict[bus]['all']),
            size=10
        )
    ))

# Overlay histograms
fig5.update_layout(
    title='Histogram of distance to the stop when the bus has arrived it',
    xaxis_title='Distance in meters',
    yaxis_title='Number of instances inside the interval',
    bargap=0.1, # gap between bars of adjacent location coordinates
    bargroupgap=0.05 # gap between bars of the same location coordinates
)
# Reduce opacity to see both histograms
fig5.update_traces(opacity=0.75)
fig5.show()

In [32]:
fig6 = go.Figure()
all_instances = []
for bus in distance_to_stop_buses_dict.keys() :
    all_instances = all_instances + distance_to_stop_buses_dict[bus]['all']

fig6.add_trace(go.Histogram(
    name='{}',
    x=all_instances,
    xbins=dict( # bins used for histogram
        start=min(all_instances),
        end=max(all_instances),
        size=10
    )
))

# Overlay histograms
fig6.update_layout(
    title='Histogram of distance to the stop when the bus has arrived it',
    xaxis_title='Distance in meters',
    yaxis_title='Number of instances inside the interval',
    bargap=0.1, # gap between bars of adjacent location coordinates
    bargroupgap=0.05 # gap between bars of the same location coordinates
)
# Reduce opacity to see both histograms
fig6.update_traces(opacity=0.75)
fig6.show()

In [33]:
#Select bus for the figure
bus = buses_given[2]
stops_x = distance_to_stop_buses_dict[bus]['stop_lons']
stops_y = distance_to_stop_buses_dict[bus]['stop_lats']
buses_x = distance_to_stop_buses_dict[bus]['bus_lons']
buses_y = distance_to_stop_buses_dict[bus]['bus_lats']

#Token and styles for the mapbox api
mapbox_access_token = 'pk.eyJ1IjoiYWxlanAxOTk4IiwiYSI6ImNrNnFwMmM0dDE2OHYzZXFwazZiZTdmbGcifQ.k5qPtvMgar7i9cbQx1fP0w'
style_day = 'mapbox://styles/alejp1998/ck6z9mohb25ni1iod4sqvqa0d'

#We create the figure object
fig7 = go.Figure()
#Add the stops to the figure
fig7.add_trace(go.Scattermapbox(
    lat=stops_y,
    lon=stops_x,
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=5,
        color='green',
        opacity=0.7
    ),
    text='',
    hoverinfo='text'
))
#Add buses to figure
fig7.add_trace(go.Scattermapbox(
    lat=buses_y,
    lon=buses_x,
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=5,
        color='black',
        opacity=0.7
    ),
    text='',
    hoverinfo='text'
))
#Lines that connect stop with bus
for i in range(len(stops_x)) :
    fig7.add_trace(go.Scattermapbox(
        lat=[stops_y[i],buses_y[i]],
        lon=[stops_x[i],buses_x[i]],
        mode='lines',
        line=dict(width=0.5, color='red'),
        text='',
        hoverinfo='text'
    ))

#And set the figure layout
fig7.update_layout(
    title='Pair bus coords when it arrives to stop vs the coords of that stop',
    height=500,
    margin=dict(r=0, l=0, t=0, b=0),
    hovermode='closest',
    showlegend=False,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=statistics.mean(stops_y + buses_y),
            lon=statistics.mean(stops_x + buses_x)
        ),
        pitch=0,
        zoom=13,
        style=style_day
    )
)

In [21]:
def bus_different_coords(df) :
    different_coords_bus_dict = {}
    for bus in df.bus.unique() : 
        bus_df = df.loc[(df.bus == bus)]
        if True : #bus_df.given_coords.min() == 1 :
            lats = []
            lons = []
            last_lat,last_lon = 0,0
            for index,row in bus_df.iterrows() :
                new_lon = row.lon
                new_lat = row.lat
                if (last_lon != new_lon) | (last_lat != new_lat) :
                    lons.append(new_lon)
                    lats.append(new_lat)
                    last_lon,last_lat = new_lon,new_lat
                    
            if len(lats) != 0 :
                different_coords_bus_dict[bus] = {}
                different_coords_bus_dict[bus]['lon'] = lons
                different_coords_bus_dict[bus]['lat'] = lats
    
    return different_coords_bus_dict

different_coords_bus_dict = bus_different_coords(experiment)

In [22]:
#Select bus for the figure
bus = buses_calc[1]
x = different_coords_bus_dict[bus]['lon']
y = different_coords_bus_dict[bus]['lat']

line_x, line_y = [],[]
for coords in list(line1.iloc[0].geometry.coords) + list(line2.iloc[0].geometry.coords) :
    if (min(x) <= coords[0] <= max(x)) & (min(y) <= coords[1] <= max(y)) :
        line_x.append(coords[0])
        line_y.append(coords[1])

#Plot figure
fig8 = go.Figure()
fig8.add_trace(go.Histogram2dContour(
        x = x,
        y = y,
        colorscale = 'Blues',
        reversescale = True,
        xaxis = 'x',
        yaxis = 'y'
    ))
fig8.add_trace(go.Scatter(
        name = 'Bus coords',
        x = x,
        y = y,
        xaxis = 'x',
        yaxis = 'y',
        mode = 'markers',
        marker = dict(
            color = 'gold',
            size = 3
        )
    ))
fig8.add_trace(go.Scatter(
        name = 'Line 1',
        x = line_x,
        y = line_y,
        xaxis = 'x',
        yaxis = 'y',
        mode = 'lines',
        line=dict(
            color = 'white',
            width=1,
        ),
        opacity=0.5
    ))
fig8.add_trace(go.Histogram(
        y = y,
        xaxis = 'x2',
        marker = dict(
            color = 'rgba(0,0,0,1)'
        )
    ))
fig8.add_trace(go.Histogram(
        x = x,
        yaxis = 'y2',
        marker = dict(
            color = 'rgba(0,0,0,1)'
        )
    ))

fig8.update_layout(
    title='2D Histogram of bus {} given coordinates'.format(bus),
    xaxis_title='Longitude',
    yaxis_title='Latitude',
    autosize = False,
    xaxis = dict(
        zeroline = False,
        domain = [0,0.85],
        showgrid = False
    ),
    yaxis = dict(
        zeroline = False,
        domain = [0,0.85],
        showgrid = False
    ),
    xaxis2 = dict(
        zeroline = False,
        domain = [0.85,1],
        showgrid = False
    ),
    yaxis2 = dict(
        zeroline = False,
        domain = [0.85,1],
        showgrid = False
    ),
    height = 800,
    width = 800,
    bargap = 0,
    hovermode = 'closest',
    showlegend = False
)

In [23]:
# Pearson correlation between distance to stop and ETA
experiment[['estimateArrive','DistanceBus']].corr(method = 'pearson')

estimateArrive  DistanceBus
estimateArrive     1.000000000  0.971850057
DistanceBus        0.971850057  1.000000000

In [24]:
# Ordinary least squares regression
model = sm.OLS(experiment.estimateArrive, experiment.DistanceBus).fit()
model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                                 OLS Regression Results                                
=======================================================================================
Dep. Variable:         estimateArrive   R-squared (uncentered):                   0.983
Model:                            OLS   Adj. R-squared (uncentered):              0.983
Method:                 Least Squares   F-statistic:                          2.252e+06
Date:                Sat, 07 Mar 2020   Prob (F-statistic):                        0.00
Time:                        12:56:07   Log-Likelihood:                     -2.4551e+05
No. Observations:               38557   AIC:                                  4.910e+05
Df Residuals:                   38556   BIC:                                  4.910e+05
Df Model:                           1                                                  
Covariance Type:            nonrobust                                                  
===============================================================================
                  coef    std err          t      P>|t|      [0.025      0.975]
-------------------------------------------------------------------------------
DistanceBus     0.3655      0.000   1500.604      0.000       0.365       0.366
==============================================================================
Omnibus:                     6176.609   Durbin-Watson:                   1.582
Prob(Omnibus):                  0.000   Jarque-Bera (JB):            10434.329
Skew:                           1.065   Prob(JB):                         0.00
Kurtosis:                       4.399   Cond. No.                         1.00
==============================================================================

Warnings:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [25]:
#Get coef for distance bus
param = model.params['DistanceBus']

In [26]:
fig9 = go.Figure()
fig9.add_trace(go.Scatter(
    x = experiment.DistanceBus,
    y = experiment.estimateArrive,
    xaxis = 'x',
    yaxis = 'y',
    mode = 'markers',
    marker = dict(
        color = 'black',
        size = 0.75
    )
))
fig9.add_shape(type="line",
    x0=0,
    y0=0,
    x1=experiment.DistanceBus.max(),
    y1=param*experiment.DistanceBus.max(),
    line=dict(
        color='gold',
        width=2,
        dash="dashdot"
    ),
)
    
# Edit the layout
fig9.update_layout(title='OLS Regression Line for ETA vs Distance Remaining to stop',
                   xaxis_title='Distance to stop(meters)',
                   yaxis_title='ETA(seconds)')

fig9.show()